<a href="https://colab.research.google.com/github/amandaliusa/cs155-kaggle/blob/master/catboost.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import AdaBoostClassifier
from sklearn.metrics import roc_curve, auc

In [2]:
import tensorflow as tf
from tensorflow.python.data import Dataset
import keras
from keras.utils import to_categorical
from keras import models
from keras import layers

Using TensorFlow backend.


In [3]:
import io
df_train = pd.read_csv('train.csv')
df_test = pd.read_csv('test.csv')

In [4]:
# replace missing values with median (less sensitive to outliers)
df_train['opened_position_qty '].fillna(df_train['opened_position_qty '].median(),inplace=True)
df_test['opened_position_qty '].fillna(df_train['opened_position_qty '].median(),inplace=True)
df_train['closed_position_qty'].fillna(df_train['closed_position_qty'].median(),inplace=True)
df_test['closed_position_qty'].fillna(df_train['closed_position_qty'].median(), inplace=True)

In [5]:
df = pd.concat([df_train,df_test],sort=False)

In [6]:
# engineer new features by grouping like features 
bid_cols = ['bid1','bid2', 'bid3', 'bid4', 'bid5']
bid_vol_cols = ['bid1vol', 'bid2vol', 'bid3vol', 'bid4vol', 'bid5vol']
ask_cols = ['ask1', 'ask2', 'ask3', 'ask4', 'ask5',]
ask_vol_cols = ['ask1vol','ask2vol', 'ask3vol', 'ask4vol', 'ask5vol']
group_cols = {"bid_cols":bid_cols,"bid_vol_cols":bid_vol_cols,"ask_cols":ask_cols,"ask_vol_cols":ask_vol_cols}

In [7]:
for group in group_cols.keys():
    print(group)
    df[f"{group}_max"] = df[group_cols[group]].max(axis=1)
    df[f"{group}_min"] = df[group_cols[group]].min(axis=1)
    df[f"{group}_spread"] = df[f"{group}_max"].div(df[f"{group}_min"])
    #df[f"{group}_logsumexp"] = df[group_cols[group]].apply(logsumexp)
    
    df[f"{group}_max"] = df[group_cols[group]].max(axis=1)
    
df["last_price_div__mid"] = df["last_price"].div(df["mid"])

bid_cols
bid_vol_cols
ask_cols
ask_vol_cols


In [8]:
x_train = df.loc[~df.y.isna()]
y_train = x_train['y']
x_train = x_train.drop(['y'], axis=1)
x_test = df.loc[df.y.isna()]
x_test = x_test.drop(['y'], axis=1)

In [9]:
# Normalize data
from sklearn import preprocessing

x_train = df_train[df_train.columns[1:27]]
y_train = df_train['y']
x_test = df_test[df_test.columns[1:]]

# Normalize training data by subtracting mean and scaling to unit variance
std_scale = preprocessing.StandardScaler().fit(x_train)
x_train_norm = std_scale.transform(x_train)
x_train = pd.DataFrame(x_train_norm, index=x_train.index, columns=x_train.columns)

# Normalize testing data by using mean and SD of training set
x_test_norm = std_scale.transform(x_test)
x_test = pd.DataFrame(x_test_norm, index=x_test.index, columns=x_test.columns) 

In [10]:
# Split training and validation data 
from sklearn.model_selection import train_test_split
x_train, x_val, y_train, y_val = train_test_split(x_train, y_train, test_size=0.2)

In [28]:
import catboost
from catboost import Pool, CatBoostClassifier
model = CatBoostClassifier(
    iterations=20000,
    learning_rate=0.03,
    boost_from_average=True,
    od_type='IncToDec',
    custom_metric='AUC',
    task_type='GPU',
)
  
model.fit(
      x_train, y_train,
      eval_set=(x_val, y_val),
      verbose=10,
)  

print(model.get_best_score())


0:	learn: 0.6502385	test: 0.6496623	best: 0.6496623 (0)	total: 16.3ms	remaining: 5m 26s
10:	learn: 0.6390226	test: 0.6388048	best: 0.6388048 (10)	total: 182ms	remaining: 5m 30s
20:	learn: 0.6326670	test: 0.6327711	best: 0.6327711 (20)	total: 346ms	remaining: 5m 28s
30:	learn: 0.6289681	test: 0.6293063	best: 0.6293063 (30)	total: 501ms	remaining: 5m 23s
40:	learn: 0.6267594	test: 0.6272833	best: 0.6272833 (40)	total: 660ms	remaining: 5m 21s
50:	learn: 0.6253438	test: 0.6260266	best: 0.6260266 (50)	total: 815ms	remaining: 5m 18s
60:	learn: 0.6244348	test: 0.6252389	best: 0.6252389 (60)	total: 976ms	remaining: 5m 19s
70:	learn: 0.6238074	test: 0.6247213	best: 0.6247213 (70)	total: 1.13s	remaining: 5m 17s
80:	learn: 0.6233767	test: 0.6243877	best: 0.6243877 (80)	total: 1.3s	remaining: 5m 19s
90:	learn: 0.6230625	test: 0.6241375	best: 0.6241375 (90)	total: 1.46s	remaining: 5m 19s
100:	learn: 0.6228159	test: 0.6239675	best: 0.6239675 (100)	total: 1.62s	remaining: 5m 18s
110:	learn: 0.6226172

920:	learn: 0.6172279	test: 0.6224455	best: 0.6224453 (918)	total: 15.2s	remaining: 5m 15s
930:	learn: 0.6171726	test: 0.6224426	best: 0.6224402 (927)	total: 15.4s	remaining: 5m 14s
940:	learn: 0.6171176	test: 0.6224420	best: 0.6224374 (935)	total: 15.5s	remaining: 5m 14s
950:	learn: 0.6170610	test: 0.6224349	best: 0.6224349 (950)	total: 15.7s	remaining: 5m 14s
960:	learn: 0.6170057	test: 0.6224310	best: 0.6224307 (958)	total: 15.9s	remaining: 5m 14s
970:	learn: 0.6169557	test: 0.6224222	best: 0.6224222 (970)	total: 16s	remaining: 5m 13s
980:	learn: 0.6169096	test: 0.6224148	best: 0.6224148 (980)	total: 16.2s	remaining: 5m 13s
990:	learn: 0.6168517	test: 0.6224085	best: 0.6224085 (990)	total: 16.3s	remaining: 5m 13s
1000:	learn: 0.6168012	test: 0.6224048	best: 0.6224017 (996)	total: 16.5s	remaining: 5m 13s
1010:	learn: 0.6167554	test: 0.6223950	best: 0.6223950 (1010)	total: 16.7s	remaining: 5m 12s
1020:	learn: 0.6166976	test: 0.6223857	best: 0.6223857 (1020)	total: 16.8s	remaining: 5m 

1830:	learn: 0.6126762	test: 0.6219070	best: 0.6219070 (1830)	total: 30.1s	remaining: 4m 58s
1840:	learn: 0.6126323	test: 0.6219070	best: 0.6219041 (1833)	total: 30.3s	remaining: 4m 58s
1850:	learn: 0.6125785	test: 0.6218995	best: 0.6218972 (1848)	total: 30.4s	remaining: 4m 58s
1860:	learn: 0.6125285	test: 0.6218796	best: 0.6218796 (1860)	total: 30.6s	remaining: 4m 58s
1870:	learn: 0.6124791	test: 0.6218715	best: 0.6218715 (1870)	total: 30.7s	remaining: 4m 57s
1880:	learn: 0.6124354	test: 0.6218690	best: 0.6218668 (1877)	total: 30.9s	remaining: 4m 57s
1890:	learn: 0.6123824	test: 0.6218612	best: 0.6218612 (1890)	total: 31.1s	remaining: 4m 57s
1900:	learn: 0.6123351	test: 0.6218539	best: 0.6218539 (1900)	total: 31.2s	remaining: 4m 57s
1910:	learn: 0.6122903	test: 0.6218514	best: 0.6218500 (1905)	total: 31.4s	remaining: 4m 57s
1920:	learn: 0.6122454	test: 0.6218454	best: 0.6218440 (1915)	total: 31.5s	remaining: 4m 56s
1930:	learn: 0.6121960	test: 0.6218382	best: 0.6218382 (1930)	total: 3

2720:	learn: 0.6085697	test: 0.6214132	best: 0.6214132 (2720)	total: 44.9s	remaining: 4m 45s
2730:	learn: 0.6085216	test: 0.6214109	best: 0.6214086 (2726)	total: 45.1s	remaining: 4m 44s
2740:	learn: 0.6084784	test: 0.6214060	best: 0.6214040 (2738)	total: 45.2s	remaining: 4m 44s
2750:	learn: 0.6084362	test: 0.6214065	best: 0.6214033 (2747)	total: 45.4s	remaining: 4m 44s
2760:	learn: 0.6083884	test: 0.6214015	best: 0.6214015 (2760)	total: 45.6s	remaining: 4m 44s
2770:	learn: 0.6083437	test: 0.6213954	best: 0.6213954 (2770)	total: 45.7s	remaining: 4m 44s
2780:	learn: 0.6083011	test: 0.6213959	best: 0.6213948 (2773)	total: 45.9s	remaining: 4m 44s
2790:	learn: 0.6082574	test: 0.6213904	best: 0.6213904 (2788)	total: 46.1s	remaining: 4m 44s
2800:	learn: 0.6082163	test: 0.6213828	best: 0.6213828 (2800)	total: 46.3s	remaining: 4m 44s
2810:	learn: 0.6081695	test: 0.6213728	best: 0.6213720 (2809)	total: 46.4s	remaining: 4m 43s
2820:	learn: 0.6081267	test: 0.6213708	best: 0.6213708 (2820)	total: 4

3610:	learn: 0.6047271	test: 0.6210709	best: 0.6210709 (3610)	total: 1m	remaining: 4m 32s
3620:	learn: 0.6046866	test: 0.6210679	best: 0.6210679 (3620)	total: 1m	remaining: 4m 32s
3630:	learn: 0.6046458	test: 0.6210643	best: 0.6210641 (3629)	total: 1m	remaining: 4m 32s
3640:	learn: 0.6045996	test: 0.6210599	best: 0.6210599 (3640)	total: 1m	remaining: 4m 32s
3650:	learn: 0.6045536	test: 0.6210521	best: 0.6210521 (3650)	total: 1m	remaining: 4m 31s
3660:	learn: 0.6045125	test: 0.6210442	best: 0.6210442 (3660)	total: 1m	remaining: 4m 31s
3670:	learn: 0.6044670	test: 0.6210323	best: 0.6210323 (3670)	total: 1m 1s	remaining: 4m 31s
3680:	learn: 0.6044259	test: 0.6210302	best: 0.6210293 (3679)	total: 1m 1s	remaining: 4m 31s
3690:	learn: 0.6043821	test: 0.6210269	best: 0.6210269 (3690)	total: 1m 1s	remaining: 4m 31s
3700:	learn: 0.6043406	test: 0.6210211	best: 0.6210208 (3697)	total: 1m 1s	remaining: 4m 31s
3710:	learn: 0.6042999	test: 0.6210189	best: 0.6210184 (3703)	total: 1m 1s	remaining: 4m

...

15880:	learn: 0.5629768	test: 0.6188664	best: 0.6188664 (15880)	total: 4m 23s	remaining: 1m 8s
15890:	learn: 0.5629470	test: 0.6188625	best: 0.6188625 (15890)	total: 4m 23s	remaining: 1m 8s
15900:	learn: 0.5629166	test: 0.6188629	best: 0.6188614 (15892)	total: 4m 23s	remaining: 1m 8s
15910:	learn: 0.5628894	test: 0.6188626	best: 0.6188605 (15905)	total: 4m 23s	remaining: 1m 7s
15920:	learn: 0.5628589	test: 0.6188660	best: 0.6188605 (15905)	total: 4m 24s	remaining: 1m 7s
15930:	learn: 0.5628297	test: 0.6188624	best: 0.6188598 (15926)	total: 4m 24s	remaining: 1m 7s
15940:	learn: 0.5628046	test: 0.6188599	best: 0.6188598 (15926)	total: 4m 24s	remaining: 1m 7s
15950:	learn: 0.5627838	test: 0.6188609	best: 0.6188582 (15946)	total: 4m 24s	remaining: 1m 7s
15960:	learn: 0.5627555	test: 0.6188550	best: 0.6188550 (15960)	total: 4m 24s	remaining: 1m 7s
15970:	learn: 0.5627257	test: 0.6188465	best: 0.6188465 (15970)	total: 4m 24s	remaining: 1m 6s
15980:	learn: 0.5626908	test: 0.6188436	best: 0.61

16750:	learn: 0.5604948	test: 0.6187776	best: 0.6187774 (16720)	total: 4m 37s	remaining: 53.9s
16760:	learn: 0.5604664	test: 0.6187823	best: 0.6187774 (16720)	total: 4m 38s	remaining: 53.8s
16770:	learn: 0.5604408	test: 0.6187803	best: 0.6187774 (16720)	total: 4m 38s	remaining: 53.6s
16780:	learn: 0.5604163	test: 0.6187797	best: 0.6187774 (16720)	total: 4m 38s	remaining: 53.4s
16790:	learn: 0.5603860	test: 0.6187782	best: 0.6187766 (16781)	total: 4m 38s	remaining: 53.3s
16800:	learn: 0.5603563	test: 0.6187824	best: 0.6187766 (16781)	total: 4m 38s	remaining: 53.1s
16810:	learn: 0.5603252	test: 0.6187866	best: 0.6187766 (16781)	total: 4m 39s	remaining: 52.9s
16820:	learn: 0.5602992	test: 0.6187856	best: 0.6187766 (16781)	total: 4m 39s	remaining: 52.8s
16830:	learn: 0.5602694	test: 0.6187840	best: 0.6187766 (16781)	total: 4m 39s	remaining: 52.6s
16840:	learn: 0.5602429	test: 0.6187782	best: 0.6187766 (16781)	total: 4m 39s	remaining: 52.4s
16850:	learn: 0.5602162	test: 0.6187802	best: 0.61

17630:	learn: 0.5579998	test: 0.6187007	best: 0.6186995 (17627)	total: 4m 52s	remaining: 39.3s
17640:	learn: 0.5579710	test: 0.6186986	best: 0.6186973 (17634)	total: 4m 52s	remaining: 39.1s
17650:	learn: 0.5579410	test: 0.6187000	best: 0.6186973 (17634)	total: 4m 52s	remaining: 39s
17660:	learn: 0.5579124	test: 0.6186985	best: 0.6186973 (17634)	total: 4m 52s	remaining: 38.8s
17670:	learn: 0.5578838	test: 0.6186948	best: 0.6186939 (17665)	total: 4m 53s	remaining: 38.6s
17680:	learn: 0.5578551	test: 0.6186926	best: 0.6186926 (17680)	total: 4m 53s	remaining: 38.5s
17690:	learn: 0.5578275	test: 0.6186899	best: 0.6186887 (17686)	total: 4m 53s	remaining: 38.3s
17700:	learn: 0.5577977	test: 0.6186869	best: 0.6186853 (17695)	total: 4m 53s	remaining: 38.1s
17710:	learn: 0.5577697	test: 0.6186877	best: 0.6186853 (17695)	total: 4m 53s	remaining: 38s
17720:	learn: 0.5577397	test: 0.6186898	best: 0.6186853 (17695)	total: 4m 53s	remaining: 37.8s
17730:	learn: 0.5577111	test: 0.6186837	best: 0.618683

18510:	learn: 0.5555359	test: 0.6186293	best: 0.6186263 (18384)	total: 5m 6s	remaining: 24.7s
18520:	learn: 0.5555070	test: 0.6186264	best: 0.6186254 (18515)	total: 5m 7s	remaining: 24.5s
18530:	learn: 0.5554777	test: 0.6186236	best: 0.6186236 (18530)	total: 5m 7s	remaining: 24.4s
18540:	learn: 0.5554500	test: 0.6186217	best: 0.6186217 (18540)	total: 5m 7s	remaining: 24.2s
18550:	learn: 0.5554175	test: 0.6186122	best: 0.6186122 (18550)	total: 5m 7s	remaining: 24s
18560:	learn: 0.5553901	test: 0.6186129	best: 0.6186118 (18553)	total: 5m 7s	remaining: 23.9s
18570:	learn: 0.5553577	test: 0.6186138	best: 0.6186116 (18564)	total: 5m 7s	remaining: 23.7s
18580:	learn: 0.5553293	test: 0.6186176	best: 0.6186116 (18564)	total: 5m 8s	remaining: 23.5s
18590:	learn: 0.5553080	test: 0.6186177	best: 0.6186116 (18564)	total: 5m 8s	remaining: 23.4s
18600:	learn: 0.5552806	test: 0.6186196	best: 0.6186116 (18564)	total: 5m 8s	remaining: 23.2s
18610:	learn: 0.5552478	test: 0.6186229	best: 0.6186116 (18564

19390:	learn: 0.5531264	test: 0.6185379	best: 0.6185339 (19272)	total: 5m 21s	remaining: 10.1s
19400:	learn: 0.5531027	test: 0.6185337	best: 0.6185332 (19398)	total: 5m 21s	remaining: 9.93s
19410:	learn: 0.5530727	test: 0.6185382	best: 0.6185332 (19398)	total: 5m 21s	remaining: 9.76s
19420:	learn: 0.5530431	test: 0.6185392	best: 0.6185332 (19398)	total: 5m 21s	remaining: 9.59s
19430:	learn: 0.5530163	test: 0.6185381	best: 0.6185332 (19398)	total: 5m 21s	remaining: 9.43s
19440:	learn: 0.5529900	test: 0.6185386	best: 0.6185332 (19398)	total: 5m 22s	remaining: 9.26s
19450:	learn: 0.5529612	test: 0.6185374	best: 0.6185332 (19398)	total: 5m 22s	remaining: 9.1s
19460:	learn: 0.5529342	test: 0.6185396	best: 0.6185332 (19398)	total: 5m 22s	remaining: 8.93s
19470:	learn: 0.5529074	test: 0.6185425	best: 0.6185332 (19398)	total: 5m 22s	remaining: 8.76s
19480:	learn: 0.5528764	test: 0.6185433	best: 0.6185332 (19398)	total: 5m 22s	remaining: 8.6s
19490:	learn: 0.5528533	test: 0.6185423	best: 0.6185

In [29]:
y_pred = model.predict(x_val)
false_positive_rate, true_positive_rate, thresholds = roc_curve(y_val, y_pred)
roc_auc = auc(false_positive_rate, true_positive_rate)
print('val auc: {}'.format(roc_auc))

val auc: 0.5632848845970767


In [30]:
from sklearn.ensemble import AdaBoostClassifier

boosting3 = AdaBoostClassifier(base_estimator=model, n_estimators=3)   
boosting3.fit(x_train, y_train)
print(boosting3.score(x_train, y_train))
print(boosting3.score(x_val, y_val))

0:	learn: 0.6516954	total: 20.6ms	remaining: 6m 51s
1:	learn: 0.6516217	total: 39.6ms	remaining: 6m 36s
2:	learn: 0.6515840	total: 57.5ms	remaining: 6m 23s
3:	learn: 0.6515466	total: 75.5ms	remaining: 6m 17s
4:	learn: 0.6515080	total: 91.7ms	remaining: 6m 6s
5:	learn: 0.6514343	total: 107ms	remaining: 5m 55s
6:	learn: 0.6513617	total: 121ms	remaining: 5m 44s
7:	learn: 0.6513250	total: 137ms	remaining: 5m 42s
8:	learn: 0.6512868	total: 152ms	remaining: 5m 38s
9:	learn: 0.6512143	total: 168ms	remaining: 5m 36s
10:	learn: 0.6511417	total: 182ms	remaining: 5m 31s
11:	learn: 0.6511041	total: 196ms	remaining: 5m 26s
12:	learn: 0.6510323	total: 211ms	remaining: 5m 24s
13:	learn: 0.6509946	total: 226ms	remaining: 5m 22s
14:	learn: 0.6509573	total: 241ms	remaining: 5m 20s
15:	learn: 0.6509209	total: 254ms	remaining: 5m 17s
16:	learn: 0.6508494	total: 268ms	remaining: 5m 14s
17:	learn: 0.6507786	total: 281ms	remaining: 5m 12s
18:	learn: 0.6507410	total: 295ms	remaining: 5m 10s
19:	learn: 0.65067

169:	learn: 0.6453194	total: 2.42s	remaining: 4m 42s
170:	learn: 0.6452924	total: 2.44s	remaining: 4m 42s
171:	learn: 0.6452648	total: 2.45s	remaining: 4m 42s
172:	learn: 0.6452363	total: 2.46s	remaining: 4m 42s
173:	learn: 0.6452074	total: 2.48s	remaining: 4m 42s
174:	learn: 0.6451804	total: 2.49s	remaining: 4m 42s
175:	learn: 0.6451526	total: 2.51s	remaining: 4m 42s
176:	learn: 0.6451242	total: 2.52s	remaining: 4m 42s
177:	learn: 0.6450971	total: 2.54s	remaining: 4m 42s
178:	learn: 0.6450690	total: 2.55s	remaining: 4m 42s
179:	learn: 0.6450415	total: 2.56s	remaining: 4m 42s
180:	learn: 0.6450149	total: 2.58s	remaining: 4m 42s
181:	learn: 0.6449869	total: 2.59s	remaining: 4m 42s
182:	learn: 0.6449589	total: 2.6s	remaining: 4m 41s
183:	learn: 0.6449315	total: 2.62s	remaining: 4m 41s
184:	learn: 0.6449040	total: 2.63s	remaining: 4m 41s
185:	learn: 0.6448770	total: 2.64s	remaining: 4m 41s
186:	learn: 0.6448497	total: 2.66s	remaining: 4m 41s
187:	learn: 0.6448224	total: 2.67s	remaining: 4

329:	learn: 0.6413360	total: 4.64s	remaining: 4m 36s
330:	learn: 0.6412947	total: 4.65s	remaining: 4m 36s
331:	learn: 0.6412725	total: 4.66s	remaining: 4m 36s
332:	learn: 0.6412514	total: 4.68s	remaining: 4m 36s
333:	learn: 0.6412307	total: 4.69s	remaining: 4m 36s
334:	learn: 0.6412087	total: 4.7s	remaining: 4m 36s
335:	learn: 0.6411870	total: 4.72s	remaining: 4m 36s
336:	learn: 0.6411465	total: 4.73s	remaining: 4m 36s
337:	learn: 0.6411250	total: 4.75s	remaining: 4m 36s
338:	learn: 0.6411034	total: 4.76s	remaining: 4m 35s
339:	learn: 0.6410817	total: 4.77s	remaining: 4m 35s
340:	learn: 0.6410609	total: 4.79s	remaining: 4m 36s
341:	learn: 0.6410405	total: 4.8s	remaining: 4m 36s
342:	learn: 0.6410197	total: 4.82s	remaining: 4m 36s
343:	learn: 0.6409976	total: 4.83s	remaining: 4m 35s
344:	learn: 0.6409775	total: 4.84s	remaining: 4m 35s
345:	learn: 0.6409567	total: 4.86s	remaining: 4m 35s
346:	learn: 0.6409359	total: 4.87s	remaining: 4m 35s
347:	learn: 0.6409149	total: 4.88s	remaining: 4m

495:	learn: 0.6379559	total: 7.02s	remaining: 4m 36s
496:	learn: 0.6379394	total: 7.03s	remaining: 4m 36s
497:	learn: 0.6379231	total: 7.05s	remaining: 4m 35s
498:	learn: 0.6379065	total: 7.06s	remaining: 4m 35s
499:	learn: 0.6378903	total: 7.08s	remaining: 4m 35s
500:	learn: 0.6378740	total: 7.09s	remaining: 4m 35s
501:	learn: 0.6378504	total: 7.1s	remaining: 4m 35s
502:	learn: 0.6378343	total: 7.12s	remaining: 4m 35s
503:	learn: 0.6378058	total: 7.13s	remaining: 4m 35s
504:	learn: 0.6377820	total: 7.14s	remaining: 4m 35s
505:	learn: 0.6377587	total: 7.16s	remaining: 4m 35s
506:	learn: 0.6377351	total: 7.17s	remaining: 4m 35s
507:	learn: 0.6377190	total: 7.18s	remaining: 4m 35s
508:	learn: 0.6376960	total: 7.2s	remaining: 4m 35s
509:	learn: 0.6376797	total: 7.21s	remaining: 4m 35s
510:	learn: 0.6376565	total: 7.23s	remaining: 4m 35s
511:	learn: 0.6376334	total: 7.24s	remaining: 4m 35s
512:	learn: 0.6376097	total: 7.25s	remaining: 4m 35s
513:	learn: 0.6375865	total: 7.27s	remaining: 4m

654:	learn: 0.6349834	total: 9.42s	remaining: 4m 38s
655:	learn: 0.6349752	total: 9.43s	remaining: 4m 38s
656:	learn: 0.6349667	total: 9.45s	remaining: 4m 38s
657:	learn: 0.6349491	total: 9.46s	remaining: 4m 38s
658:	learn: 0.6349412	total: 9.47s	remaining: 4m 38s
659:	learn: 0.6349285	total: 9.49s	remaining: 4m 38s
660:	learn: 0.6349112	total: 9.51s	remaining: 4m 38s
661:	learn: 0.6348938	total: 9.52s	remaining: 4m 38s
662:	learn: 0.6348763	total: 9.53s	remaining: 4m 38s
663:	learn: 0.6348591	total: 9.55s	remaining: 4m 38s
664:	learn: 0.6348466	total: 9.56s	remaining: 4m 38s
665:	learn: 0.6348338	total: 9.58s	remaining: 4m 38s
666:	learn: 0.6348218	total: 9.6s	remaining: 4m 38s
667:	learn: 0.6348042	total: 9.61s	remaining: 4m 38s
668:	learn: 0.6347958	total: 9.63s	remaining: 4m 38s
669:	learn: 0.6347790	total: 9.64s	remaining: 4m 38s
670:	learn: 0.6347668	total: 9.66s	remaining: 4m 38s
671:	learn: 0.6347493	total: 9.67s	remaining: 4m 38s
672:	learn: 0.6347371	total: 9.69s	remaining: 4

...

19243:	learn: 0.6924407	total: 4m 21s	remaining: 10.3s
19244:	learn: 0.6924407	total: 4m 21s	remaining: 10.3s
19245:	learn: 0.6924405	total: 4m 21s	remaining: 10.2s
19246:	learn: 0.6924407	total: 4m 21s	remaining: 10.2s
19247:	learn: 0.6924405	total: 4m 21s	remaining: 10.2s
19248:	learn: 0.6924405	total: 4m 21s	remaining: 10.2s
19249:	learn: 0.6924405	total: 4m 21s	remaining: 10.2s
19250:	learn: 0.6924405	total: 4m 21s	remaining: 10.2s
19251:	learn: 0.6924403	total: 4m 21s	remaining: 10.2s
19252:	learn: 0.6924403	total: 4m 21s	remaining: 10.1s
19253:	learn: 0.6924402	total: 4m 21s	remaining: 10.1s
19254:	learn: 0.6924402	total: 4m 21s	remaining: 10.1s
19255:	learn: 0.6924401	total: 4m 21s	remaining: 10.1s
19256:	learn: 0.6924400	total: 4m 21s	remaining: 10.1s
19257:	learn: 0.6924401	total: 4m 21s	remaining: 10.1s
19258:	learn: 0.6924401	total: 4m 21s	remaining: 10.1s
19259:	learn: 0.6924400	total: 4m 21s	remaining: 10.1s
19260:	learn: 0.6924398	total: 4m 21s	remaining: 10s
19261:	learn

19397:	learn: 0.6924359	total: 4m 23s	remaining: 8.18s
19398:	learn: 0.6924357	total: 4m 23s	remaining: 8.16s
19399:	learn: 0.6924358	total: 4m 23s	remaining: 8.15s
19400:	learn: 0.6924357	total: 4m 23s	remaining: 8.13s
19401:	learn: 0.6924358	total: 4m 23s	remaining: 8.12s
19402:	learn: 0.6924358	total: 4m 23s	remaining: 8.11s
19403:	learn: 0.6924358	total: 4m 23s	remaining: 8.09s
19404:	learn: 0.6924357	total: 4m 23s	remaining: 8.08s
19405:	learn: 0.6924357	total: 4m 23s	remaining: 8.07s
19406:	learn: 0.6924357	total: 4m 23s	remaining: 8.05s
19407:	learn: 0.6924357	total: 4m 23s	remaining: 8.04s
19408:	learn: 0.6924357	total: 4m 23s	remaining: 8.03s
19409:	learn: 0.6924356	total: 4m 23s	remaining: 8.01s
19410:	learn: 0.6924355	total: 4m 23s	remaining: 8s
19411:	learn: 0.6924355	total: 4m 23s	remaining: 7.99s
19412:	learn: 0.6924354	total: 4m 23s	remaining: 7.97s
19413:	learn: 0.6924355	total: 4m 23s	remaining: 7.96s
19414:	learn: 0.6924354	total: 4m 23s	remaining: 7.94s
19415:	learn:

19554:	learn: 0.6924305	total: 4m 25s	remaining: 6.04s
19555:	learn: 0.6924305	total: 4m 25s	remaining: 6.03s
19556:	learn: 0.6924304	total: 4m 25s	remaining: 6.02s
19557:	learn: 0.6924304	total: 4m 25s	remaining: 6s
19558:	learn: 0.6924304	total: 4m 25s	remaining: 5.99s
19559:	learn: 0.6924300	total: 4m 25s	remaining: 5.98s
19560:	learn: 0.6924302	total: 4m 25s	remaining: 5.96s
19561:	learn: 0.6924302	total: 4m 25s	remaining: 5.95s
19562:	learn: 0.6924302	total: 4m 25s	remaining: 5.94s
19563:	learn: 0.6924302	total: 4m 25s	remaining: 5.92s
19564:	learn: 0.6924302	total: 4m 25s	remaining: 5.91s
19565:	learn: 0.6924300	total: 4m 25s	remaining: 5.89s
19566:	learn: 0.6924301	total: 4m 25s	remaining: 5.88s
19567:	learn: 0.6924299	total: 4m 25s	remaining: 5.87s
19568:	learn: 0.6924298	total: 4m 25s	remaining: 5.85s
19569:	learn: 0.6924296	total: 4m 25s	remaining: 5.84s
19570:	learn: 0.6924296	total: 4m 25s	remaining: 5.83s
19571:	learn: 0.6924298	total: 4m 25s	remaining: 5.81s
19572:	learn:

19705:	learn: 0.6924249	total: 4m 27s	remaining: 3.99s
19706:	learn: 0.6924249	total: 4m 27s	remaining: 3.98s
19707:	learn: 0.6924248	total: 4m 27s	remaining: 3.97s
19708:	learn: 0.6924249	total: 4m 27s	remaining: 3.95s
19709:	learn: 0.6924248	total: 4m 27s	remaining: 3.94s
19710:	learn: 0.6924248	total: 4m 27s	remaining: 3.92s
19711:	learn: 0.6924248	total: 4m 27s	remaining: 3.91s
19712:	learn: 0.6924247	total: 4m 27s	remaining: 3.9s
19713:	learn: 0.6924247	total: 4m 27s	remaining: 3.88s
19714:	learn: 0.6924246	total: 4m 27s	remaining: 3.87s
19715:	learn: 0.6924245	total: 4m 27s	remaining: 3.86s
19716:	learn: 0.6924245	total: 4m 27s	remaining: 3.84s
19717:	learn: 0.6924245	total: 4m 27s	remaining: 3.83s
19718:	learn: 0.6924245	total: 4m 27s	remaining: 3.82s
19719:	learn: 0.6924245	total: 4m 27s	remaining: 3.8s
19720:	learn: 0.6924242	total: 4m 27s	remaining: 3.79s
19721:	learn: 0.6924242	total: 4m 27s	remaining: 3.78s
19722:	learn: 0.6924242	total: 4m 27s	remaining: 3.76s
19723:	learn

19855:	learn: 0.6924197	total: 4m 29s	remaining: 1.96s
19856:	learn: 0.6924196	total: 4m 29s	remaining: 1.94s
19857:	learn: 0.6924194	total: 4m 29s	remaining: 1.93s
19858:	learn: 0.6924196	total: 4m 29s	remaining: 1.92s
19859:	learn: 0.6924196	total: 4m 29s	remaining: 1.9s
19860:	learn: 0.6924194	total: 4m 29s	remaining: 1.89s
19861:	learn: 0.6924194	total: 4m 29s	remaining: 1.87s
19862:	learn: 0.6924194	total: 4m 29s	remaining: 1.86s
19863:	learn: 0.6924193	total: 4m 29s	remaining: 1.85s
19864:	learn: 0.6924191	total: 4m 29s	remaining: 1.83s
19865:	learn: 0.6924191	total: 4m 29s	remaining: 1.82s
19866:	learn: 0.6924190	total: 4m 29s	remaining: 1.81s
19867:	learn: 0.6924190	total: 4m 29s	remaining: 1.79s
19868:	learn: 0.6924190	total: 4m 29s	remaining: 1.78s
19869:	learn: 0.6924189	total: 4m 29s	remaining: 1.77s
19870:	learn: 0.6924190	total: 4m 29s	remaining: 1.75s
19871:	learn: 0.6924189	total: 4m 29s	remaining: 1.74s
19872:	learn: 0.6924189	total: 4m 29s	remaining: 1.73s
19873:	lear

In [31]:
y_pred = boosting3.predict(x_val)
false_positive_rate, true_positive_rate, thresholds = roc_curve(y_val, y_pred)
roc_auc = auc(false_positive_rate, true_positive_rate)
print('val auc: {}'.format(roc_auc))

val auc: 0.5511375181775524


In [32]:
df_test['Predicted'] = boosting3.predict_proba(x_test)[:,1]
df_test[["id","Predicted"]].to_csv('submission_cat_4.csv')